---
CSC 268 Homweork 3:  Edge Detection
---

This homework will give you some practice working with classic edge detection algorithms.  You will get a feel for how their parameters should be adjusted, in addition to some of their limitations.  As a note, you can find many implementations of these algorithms on the internet.  Please resist the urge to copy from an existing implementation, since you will learn very little from doing so.  As a reminder, you are asked to cite any sources used (other than the textbook) during preparation of this homework.

In [1]:
import math
import cv2 as cv
import numpy as np
import matplotlib.pyplot as plt
import matplotlib as mpl
mpl.rc('image', cmap='gray')

def imshow(img,title=None):
    plt.figure(figsize=(10,6))
    plt.imshow(img)
    plt.axis('off')
    if title:
        plt.title(title)
    plt.show()

### Part One:  Marr-Hildreth Edge Detection

Marr-Hildreth edge detection is unusual for looking at the second derivative rather than the first.  Since edges should  be maxima of the first derivative, the second derivative will change sign on every edge.  Thus we can look for zero-crossings of the second derivative to locate edges.  (Usually, candidate edges identified through these means will be thresholded based on the magnitude of the first derivative, to avoid picking out edges that are too faint to be significant.)

To implement Marr-Hildreth, first process the image with a Laplacian-of-Gaussian (LoG) filter. (You can use the simple Laplacian filter we learned in class, or try the larger filter 9x9 described [here](https://homepages.inf.ed.ac.uk/rbf/HIPR2/log.htm) which should give better results.)  Next, mark a pixel as a potential edge if the LoG result differs in sign from the pixel to the left or above.  Finally, keep as edges only those candidates where the gradient magnitude also exceeds a chosen threshold.

**To Do:**  For this section, you should write a function that takes an image file and threshold value as arguments, and outputs an edge image.  Test your function on at least three images of your choice, showing the results below.  Include the threshold value in the title line of the image.  (There are a number of web sites offering royalty-free photographs that you can look at for candidates.)

As you evaluate the results, keep in mind that it may not be possible to see all the edges when a high resolution image is displayed in a small space.  The `imshow` function above includes a line to set the figure size; you should set it to the largest amount that fits on your screen.  Or course, this may still not be enough for some very high resolution images, so you may have to downsample or resort to scrolling.

### Part Two:  Canny Edge Detection

Canny edge detection is a fairly simple algorithm that is quick to compute and gives pretty effective results.  It incorporates several extra steps that improve the quality of the results.  First, it localizes edges by requiring that any edge point is a local maximum in the gradient direction.  Put another way, if you look at the two neighboring pixels on either side of the current pixel, the central pixel must have the largest gradient magnitude.  To figure out which neighbors to look at, you will follow the direction of the gradient.  There are four options:  either you will look at the north/south pair, or the east/west pair, or northeast/southwest, or southeast/northwest.  It decides which one by rounding the gradient direction to the nearest multiple of 45 degrees.

The other novel idea introduced by Canny is the use of two threshold levels, one high and one low, in a procedure sometimes called hysteresis.  The motivation for this step is to recover complete edges, even if some portions of the edge are less distinct than others.  Once candidate edges are identified via the local maximum criterion, the gradient magnitude at each point is tested using the high threshold.  Any candidate exceeding this value is immediately declared an edge.  Next, the points are tested again using the low threshold.  Points in this group that exceed the low threshold may be declared as edges, but only if they are part of a connected cluster that touches an already-identified edge.  Points below the threshold, or part of a group that does not touch any high-threshold edges, are discarded.

To summarize, here are the steps you should follow:
1. Smooth the image slightly, using Gaussian kernel with a small radius.  You can use the simple kernel we showed in class, or call OpenCV's `getGaussianKernel` function which accepts a radius as argument.  (OpenCV also has a `gaussianBlur` function that does everything in one step.  For learning purpose, let's apply the kernel ourselves this time.)
2. Compute the gradient components using an edge filter.
3. Compute the gradient angle and round to the nearest multiple of 45 degrees (a.k.a. pi/4 radians).  (Numpy's `mod` and `round` functions may be useful here.)
4. Based on the results of the previous step, determine for each pixel whether it is a local maximum.  One way to do this is to process the image in four separate steps, one for each of the possible neighbor directions.  You may find it helpful to pad the image beforehand to avoid edge effects.  You'll want to use NumPy's `greater` function or something similar.
5. Apply the high threshold and combine it with the candidate map from the previous step.
6. Apply the low threshold and identify components that touch the previously identified edges.  You can do this using a maze traversal approach, or you can apply the connected components technique that we will learn next week, implemented in `scipy.ndimage.label`.  Numpy's `bincount` may also be useful.
7. Return a binary image showing all the identified edges.

**To Do:**  For this section, you should write a function that takes an image file, Gaussian blur radius, and two threshold values as arguments, and outputs an edge image.  Test your function on at least five images of your choice, showing the results below.  Include the parameter values in the title line of the image.  (There are a number of web sites offering royalty-free photographs that you can look at for candidates.)

If you want more detail on the algorithm, you can read the [Wikipedia article](https://en.wikipedia.org/wiki/Canny_edge_detector).  To test your own implementation, you can compare results with OpenCV's `Canny` function.

### Reflection

Write a reflection on this assignment.  What was hard?  What did you learn?  What are your observations on how to choose good parameters?